# Make an auto playlist!

In [57]:
#Mel frequency: m = 2595 log10(1 + f/700)
#The cepstrum is the result of taking the Fourier Transform of the logarithm of the estimated power spectrum of a signal.
#Mel Frequency Cepstral Coefficents (MFCCs) are a feature widely used in automatic speech and speaker recognition. 
#They were introduced by Davis and Mermelstein in the 1980's

#Training the CNN is then performed on log-compressed Mel spectrograms (128 frequency bands, window size of 23 ms, 
#50% window overlap), computed from randomly sampled 3-second-clips of the audio snippets. 

In [58]:
import spotipy
import spotipy.util as util
from spotipy.oauth2 import SpotifyClientCredentials

import os
import csv

In [59]:
scope = 'user-library-read'
# You can get credentials from https://developer.spotify.com/dashboard/applications
username = 'retrojetpacks'
client_id='c4a5beba2e394f64a02d05f217153120'
client_secret='f5976fdcea2443d4b1248ac879912e8a'
redirect_uri='https://localhost'



In [60]:
playlist_dir = "C:/Users/Colin/Documents/Playlist maker/spotify_playlists/"

In [61]:
def get_token():
    token = util.prompt_for_user_token(username,scope, client_id, client_secret, redirect_uri)
    sp = spotipy.Spotify(token, requests_timeout=10)
    return sp

In [62]:
#alphabet1 = ['a','b','c','d','e','f','g','h','i','j', 'k','l','m','n','o','p','q','r','s','t','u','v','w','x','y','z']
alphabet1 = ['a','e','f','g','h','i','j', 'k','l','m','n','o','p','q','r','s','t','u','v','w','x','y','z']
alphabet2 = ['a','b','c','d','e','f','g','h','i','j','k','l','m','n','o','p','q','r','s','t','u','v','w','x','y','z']
perPage = 50
Npage   = 200 #Goal 10,000 in total



In [63]:
def get_tracks(sp, playlists):
    rows = []
    
    for play in playlists['playlists']['items']:
        #print(play['name'])
        if play['name'][:7] != 'This Is':
            rows.append([play['name']])
            try:
                tracks = sp.playlist(play['id'], additional_types=('track', ))['tracks']['items']
            except spotipy.client.SpotifyException:
                sp = get_token()
                try:
                    tracks = sp.playlist(play['id'], additional_types=('track', ))['tracks']['items']
                except:
                    print("Can't access tracks")
            except Exception as e:
                print("Exception while loading tracks")
                print(e)
                break

            #Scan all tracks in a playlist
            artists = []
            for track in tracks:
                tr = track['track']

                try:
                    artist = tr['artists'][0]['name']
                    rows.append([
                        artist, 
                        tr['name'], 
                        tr['id'], 
                        tr['preview_url']
                        ])
                except: 
                    artist = ''
                    print("Song row failed")
                artists.append(artist)
            rows.append([''])

            #Do not save if playlist contains many repeated artists
            if len(set(artists)) < len(artists) / 5:
                print('Duplicate artists: ' + play['name'] + ' - ' + artists[0])
                rows = []

    return rows, sp

# Search for playlists and extract tracks

In [64]:
max_count = 10

sp = get_token()
print("Starting playlist scouring")

for let1 in alphabet1:
    #Load csv file for saving
    with open(playlist_dir+'playlists_'+let1+'.csv', 'w', newline='', encoding='utf-8') as file:
        writer = csv.writer(file, delimiter='|')
        
        for let2 in alphabet2:
            try:
                playlists = sp.search(let1+let2, perPage, 0, type='playlist')
            except spotipy.client.SpotifyException:
                sp = get_token()
                try:
                    playlists = sp.search(let1+let2, perPage, 0, type='playlist')
                except:
                    pass
            except:
                print("Failure to load, skipping this playlist")
                pass
            count = 0

            while count < max_count:
                if playlists:
                    rows, sp = get_tracks(sp, playlists)
                else:
                    rows = []
                writer.writerows(rows)

                #if 'next' in playlists['playlists']:
                if playlists:
                    try:
                        playlists = sp.next(playlists['playlists'])
                    except spotipy.client.SpotifyException:
                        get_token()
                        try:
                            playlists = sp.next(playlists['playlists'])
                        except:
                            print("Unable to find more playlists. Moving on...")
                            pass
                    count += 1
                else: 
                    count = max_count

                print(let1+let2, count)


Starting playlist scouring
Duplicate artists: aaa - tklensta03
Duplicate artists: AAAファンが選ぶライブで盛り上がる曲TOP10 - AAA
Duplicate artists: Aaliyah - Aaliyah
Song row failed
Duplicate artists: AAA バラード - AAA
Duplicate artists: AAM SpotifySundays | with David Blackadder - Wolfgang Amadeus Mozart
Duplicate artists: Aaron y su Grupo Ilusion Exitos - Aaron Y Su Grupo Ilusion
Duplicate artists: AaMusicOnlyFans - Ulug'bek Rahmatullaev
Duplicate artists: Aamir's Renditions - Aamir
Duplicate artists: Tripple AaA - Dj Prinz Money
aa 1
Song row failed
Song row failed
Duplicate artists: AAA全曲 - AAA
Duplicate artists: OST AADC - Melly Goeslaw
Duplicate artists: LOVE AAJ KAL 2 - Pritam
Duplicate artists: Shakira Singles Playlist (ft Me Gusta by Shakira & Anuel AA)  - Shakira
Duplicate artists: Aamir's Originals - Aamir
aa 2
Duplicate artists: Anuel AA álbum 2020 (Enmanuel) - Anuel AA
Duplicate artists: Aaron Lewis - State I'm In - Aaron Lewis
Duplicate artists: Dancing Aaron Smith - Aaron Smith
Duplicate a

Duplicate artists: Elefante-El abandonado - Elefante
Duplicate artists: ABC kids songs - Nursery Rhymes and Kids Songs
Song row failed
Duplicate artists: Leonie - Abenteuer auf vier Hufen  - Christian Mörken
Duplicate artists: Everyone is talking about Jamie - Original West End Cast of Everybody's Talking About Jamie
Duplicate artists: Summer Of Like/Songs about Mikey Way by Peter Wentz - Fall Out Boy
Duplicate artists: Bhimsen Joshi Suprasiddha - Bhimsen Joshi
Duplicate artists: ABBA – Mamma Mia (Original Soundtrack) - ABBA
Duplicate artists: Pa Que Se Mojen Todas (Album) - Abraham Vazquez - Abraham Vazquez
Duplicate artists: mamma mia but ABBA - ABBA
ab 8
Duplicate artists: Abel The Kid & Raul Ortiz History - Abel The Kid
Duplicate artists: Dong Abay — Perpekto - Dong Abay
Duplicate artists: Paul Heaton and Jackie Abbot  - Paul Heaton
Song row failed
Duplicate artists: Ceramah ustadz abdul somad - dakwah.me - Ustadz Adi Hidayat
Duplicate artists: Hörspielzeit: Paw Patrol - PAW Patrol

Duplicate artists: Adkiw y cartel - Akwid
Duplicate artists: Jesús Adrián Romero - Musica Cristiana - Jesús Adrián Romero
Duplicate artists: Brian Adams - Bryan Adams
Duplicate artists: LOS ADOLESCENTES - Adolescent's Orquesta
Duplicate artists: JoJo's Bizzare Adventure [FULL SOUNDTRACK] - Hiroaki Tommy Tominaga
ad 1
Duplicate artists: Adolescentes - Exitos - Adolescent's Orquesta
Duplicate artists: ADELE EXITOS - Adele
Duplicate artists: Adoracion para orar - Esperanza de Vida
Duplicate artists: Brayan Adams - Bryan Adams
Duplicate artists: Ada band full album - Ada Band
Duplicate artists: Ebit G Ade - Ebiet G. Ade
Duplicate artists: Adwin - Akwid
Duplicate artists: aditya sofyan - Adhitia Sofyan
Duplicate artists: LA ADICTIVA EXITOS - La Adictiva Banda San José de Mesillas
Duplicate artists: Jesus Adrian Romero Exitos - Jesús Adrián Romero
Duplicate artists: Adele Playlist - Adele
Duplicate artists: Exitos de Jesus Adrian Romero - Jesús Adrián Romero
Duplicate artists: The Adams Fami

Song row failed
Duplicate artists: AETCTBØ - Rauf & Faik
ae 3
Song row failed
Duplicate artists: Aerobic 120 bpm - Workout Music Tv
Duplicate artists: Aectbo - Rauf & Faik
Song row failed
Duplicate artists: step aerobics 128 bpm - Workout Remix Factory
Song row failed
Song row failed
Song row failed
ae 4
Duplicate artists: Best of Aerosmith - Aerosmith
Duplicate artists: Aerosmith Best of - Aerosmith
Song row failed
Song row failed
Song row failed
Song row failed
Song row failed
Song row failed
Song row failed
Song row failed
Song row failed
Song row failed
Song row failed
Song row failed
Song row failed
Song row failed
Song row failed
Song row failed
Song row failed
Song row failed
Song row failed
Song row failed
Song row failed
Song row failed
Song row failed
Song row failed
Song row failed
Song row failed
Song row failed
Song row failed
Song row failed
Song row failed
Song row failed
Song row failed
Song row failed
Song row failed
Song row failed
Song row failed
Song row failed
Song

Duplicate artists: AFL THEME SONGS - Footy Fever Themes
Duplicate artists: Afro Trap Pt. 1-10 (MHD) - MHD
Song row failed
Song row failed
Song row failed
Song row failed
Song row failed
Song row failed
Song row failed
Song row failed
Song row failed
Song row failed
Song row failed
Song row failed
Song row failed
Song row failed
Song row failed
Song row failed
Song row failed
Song row failed
Song row failed
Song row failed
Song row failed
Song row failed
Song row failed
Song row failed
Song row failed
Song row failed
Song row failed
Song row failed
Song row failed
Song row failed
Song row failed
Song row failed
Song row failed
Song row failed
Song row failed
Song row failed
Song row failed
Song row failed
Song row failed
Song row failed
Song row failed
Song row failed
Song row failed
Song row failed
Song row failed
Song row failed
Song row failed
Song row failed
Song row failed
Song row failed
Song row failed
Song row failed
Song row failed
Song row failed
Song row failed
Song row faile

...

Duplicate artists: Beats DJ Zone, Sonicko, Verse... - Red Bull Batalla de los Gallos
Duplicate artists: Ministério Zoe completo - Ministério Zoe
Duplicate artists: ZONKE TOP TRACKS - Zonke
Duplicate artists: Kronno Zomber - Kronno Zomber
Duplicate artists: ZOÉ - Labios Rotos - Zoé
zo 5
Duplicate artists: Yellow Zone - Hilton Trantow Iebra
Duplicate artists: crono zomber - Kronno Zomber
Duplicate artists: Green Zone - Domingo Tomey
Duplicate artists: Blue Zone - Guiomar Perales
Duplicate artists: Kinderen voor Kinderen - Beste van - Kinderen voor Kinderen
Duplicate artists: Krono Zomber - Kronno Zomber
Duplicate artists: ZOO - Totes les cançons / All songs / Todas las canciones - ZOO
Duplicate artists: The Adventure Zone - Balance - The Adventure Zone
Duplicate artists: Zodiaco – Moderatto - Moderatto
Duplicate artists: Zola 7 - Zola
zo 6
Duplicate artists: Zoey's Extraordinary Playlist (in order) - Cast of Zoey’s Extraordinary Playlist
Duplicate artists: Aspencat / La Raiz / ZOO - Aspe

Duplicate artists: D' ZRT - D'ZRT
Duplicate artists: Zro Albums - Z-Ro
Duplicate artists: Old Zro-Radio - Z-Ro
Duplicate artists: ZR RAMALHO - Zé Ramalho
Duplicate artists: Zro crack - Z-Ro
Duplicate artists: zro screwed - Z-Ro
Duplicate artists: ZRO - Z-Ro
zr 1
Duplicate artists: zro and trae - Z-Ro
Duplicate artists: ALL-ESSO - Alesso
Duplicate artists: Introducing: Smith & Thell - Smith & Thell
Duplicate artists: RAPTUS - Nayt
Duplicate artists: ZRO - Z-Ro
Duplicate artists: Zro - Z-Ro
Duplicate artists: COMPLETE SAYGRACE - SAYGRACE
Duplicate artists: ZrZy - P T K
Duplicate artists: Zro mo city don - Z-Ro
Duplicate artists: ZRO KOTG - Z-Ro
zr 2
Duplicate artists: ZRO Albums mix - Z-Ro
Duplicate artists: zro meth - Z-Ro
Song row failed
Song row failed
zr 3
Duplicate artists: Zro - Z-Ro
Song row failed
Song row failed
Song row failed
Duplicate artists: Lil Ricky ZR3 King King - Oliver Tree
zr 4
Song row failed
Duplicate artists: zro - Z-Ro
Duplicate artists: Zro - Agonylife
Duplicate 

Duplicate artists: Weihnachtslieder Rolf Zukowski - Rolf Zuckowski
Duplicate artists: Zucchero best of - Zucchero
Duplicate artists: Kindergeschichten zum Relaxen - Yasemin Kehali
Duplicate artists: Wer sagt das?! Zugabe! – Alles von Ben Zucker - Ben Zucker
Duplicate artists: Kinderlieder zum Einschlafen - Simone Sommerland
Duplicate artists: Jarow's Horror-Stories zum Einschlafen (Stundenlang)  - Jarow
zu 2
Duplicate artists: Rolf Zuckowski – Best of - Rolf Zuckowski
Duplicate artists: Märchen zum Einschlafen - Brüder Grimm
Duplicate artists: Best of Zubeen Garg - Zubeen Garg
Duplicate artists: zuchero - Zucchero
Duplicate artists: Lo Mejor De Alex Zurdo - Alex Zurdo
zu 3
Duplicate artists: REGEN / Gewitter (10 Stunden) zum Schlafen, ASMR   - Silent Chills
Duplicate artists: Einschlafmusik – Effektive Musik zum Einschlafen und Durchschlafen | Entspannungsmusik | Yogamusik - Ingvi Aronsson
Duplicate artists: Staubsauger (Geräusch für dein Baby zum Einschlafen) - Jolma
Duplicate artists

zv 4
Song row failed
Duplicate artists: ako ovo slusam znaci da spavam - Makiko Hirohashi
Duplicate artists: Z.Viki - The Weeknd
Duplicate artists: jc_zvmorv - Drake
Duplicate artists: tvrdej zvuk pico - Ghostemane
Duplicate artists: Dzeny - Zena Zvijer FULL ALBUM + bonus songs - Dzeny
Duplicate artists: 100 zvířat - Sto zvířat
Song row failed
zv 5
Duplicate artists: Faina Faina – Žilvinas Žvagulis - Žilvinas Žvagulis
Duplicate artists: Zviegtin zviedza kumeļaiši - Vilki un Atbalstitaji
Duplicate artists: Zv o original - Zé Vaqueiro
Song row failed
Duplicate artists: zvyb - A Boogie Wit da Hoodie
Duplicate artists: Zvracení  - Arch Enemy
zv 6
Duplicate artists: Nikdy Nic Nebylo – Sto zvířat - Sto zvířat
Song row failed
Duplicate artists: zvϟ's list 🤘🏼 - Black Sabbath
Duplicate artists: ZVNI🇸🇪 - Yasin
zv 7
Duplicate artists: 🚨ZV🚨 - Ziedu Vija
Duplicate artists: radio glava i zvukova mladej - Radiohead
Song row failed
Song row failed
Song row failed
Song row failed
Song row failed
Duplic

Duplicate artists: Lil nate new zydeco - Lil' Nathan & The Zydeco Big Timers
Duplicate artists: Ballady o Kurde życiu - Krulig
Duplicate artists: Przejebane życie  - Lil Peep
Duplicate artists: Buckwheat Zydeco Best Of - Buckwheat Zydeco
zy 2
Duplicate artists: Percy Jackson/Helden des Olymp/Rick Riodan - Percy Jackson
Song row failed
Duplicate artists: Psygressive Concept by ZYCE  - Zyce
Duplicate artists: Podcast | 呱吉 新資料夾 - 呱吉
Song row failed
zy 3
Song row failed
Duplicate artists: SLATT ZY - Slatt Zy
Duplicate artists: Zydeco - Chris Ardoin
Duplicate artists: krokodyl w żyłach - 2Pac
zy 4
Duplicate artists: Oliver's music zyzz - The Neighbourhood
Duplicate artists: żyrandol - Taco Hemingway
Duplicate artists: ZY. Evolution - Polo G
Duplicate artists: Perry Rhodan 6. Zyklus-M87 - K. H. Scheer
Duplicate artists: ..  Podwójne Życie Weroniki - ZBIGNIEW PREISNER  .. - Zbigniew Preisner
Duplicate artists: Paco de Lucía  Zyriab - Paco de Lucía
zy 5
Duplicate artists: Kai Meyer - Merle-Zyk